# 3D shapes management - Demo notebook 

This notebook gives an insight on how we dealt with 3d shapes along this project.

The shapes we had were encoded as triangle meshes and encoded in `.off` files. Meshes are convenient to visualize thanks to an integretated feature of plotly, that allows us to see the shapes in 3d with lighting and to manipulate them.

The Wasserstein barycenters algorithm requires a probability distribution in the space for the shape, so we built a tool that constructs the interior of the surface described by the triangular meshes.

Then, as an output of the algorithm, we obtain a point cloud. We couldn't project light on point clouds, making it hard to observe the result of our experiment. So we built another tool that allows us to reconstruct a mesh out the point cloud.

## Imports

In [1]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from wasserstein_barycenters.utils import read_off, mesh_to_point_cloud, rescale, point_cloud_to_mesh

## Data importation

In [123]:
# path to data
path_to_meshes = "data/meshes/"
path_to_numpy = "data/numpy/"

In [2]:
figname = "torus" # Modify this to see the process on a different figure

In [126]:
original_vertices, original_faces = read_off(path_to_meshes + figname + ".off")
original_vertices = rescale(original_vertices, 0.01, 0.99)

## Space definition

In [125]:
N = 100
t = np.linspace(0, 1, N)
space = np.stack(np.meshgrid(t, t, t), axis=-1).reshape(N**3, -1)

## Mesh to point cloud to mesh

In [127]:
# Mesh to point cloud
point_cloud = mesh_to_point_cloud(space, original_vertices, original_faces)
np.save(path_to_numpy + figname + ".npy", point_cloud.reshape(N, N, N))
points_inside = (point_cloud.reshape(N**3, -1) > 0.5).flatten()
cloud_x = space[points_inside][:, 0]
cloud_y = space[points_inside][:, 1]
cloud_z = space[points_inside][:, 2]

# Point cloud to mesh
reconstructed_vertices, reconstructed_faces = point_cloud_to_mesh(points_inside.reshape(N,N,N), space)

100%|██████████| 576/576 [00:30<00:00, 18.77it/s]
Reconstructing surface: 100%|██████████[00:00<00:00]


## Results

In [128]:
fig = make_subplots(rows=1, cols=3, specs=[[{"type": "scatter3d"} for _ in range(3)]], subplot_titles=("Original", "Point cloud", "Reconstructed"))

fig.add_trace(
        go.Mesh3d(
            x=original_vertices[:, 0],
            y=original_vertices[:, 1],
            z=original_vertices[:, 2],
            i=original_faces[:, 0],
            j=original_faces[:, 1],
            k=original_faces[:, 2],
        ), row=1, col=1
)
fig.add_trace(
    go.Scatter3d(x=cloud_x, y=cloud_y, z=cloud_z, mode='markers'), row=1, col=2
)
fig.add_trace(
    go.Mesh3d(
            x=reconstructed_vertices[:, 0],
            y=reconstructed_vertices[:, 1],
            z=reconstructed_vertices[:, 2],
            i=reconstructed_faces[:, 0],
            j=reconstructed_faces[:, 1],
            k=reconstructed_faces[:, 2],
        ), row=1, col=3
)
fig.update_layout(height=400, width=1200, title_text="Mesh to point cloud to mesh workflow", title_x=0.5)
fig.update_scenes(
            xaxis_visible=False, yaxis_visible=False, zaxis_visible=False
        )

## Discussion

This process is efficient for simple shapes, but it can be instable for more complex shapes (try with `figname = "bull"` or `"duck"` for instance).